# Compare reflecitivity results from different calculations

    1- Classic 1D specular reflectivity
   
    2- Constant-Q summing for 1D specular reflectivity
   
    3- Summing the specular ridge after computing the off-specular in (kf_z - kf_i) vs Qz with simple rebinning.
    This approach just computes (kf_z - kf_i) and Qz for each pixel and TOF bin and histograms them.
   
    4- The "smoothing" approach, which is similar to 3, but applies Gaussian smoothing on top. This was the approach followed in QuickNXS 1.0. It produces a smooth image of the off-specular signal but doesn't provide errors for data analysis and can't be modeled directly.
    
The different calculations are compared for a TOF binning of 40 usec and 400 usec to see the effect of TOF binning on the final reflectivity curve.

All calculations use SANGLE.

In [2]:
import os
import numpy as np
import scipy.stats
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode(connected=True)

import warnings
warnings.filterwarnings('ignore', module='numpy')
warnings.filterwarnings('ignore')

In [3]:
import sys
sys.path.append("/SNS/users/m2d/git/reflectivity_ui/test/notebooks")
from plot_utils import plot1d, plot_heatmap

In [4]:
def load_data(file_path, index=75, q_axis=True, width=0):
    offspec_data = np.loadtxt(file_path)
    print offspec_data.shape

    unique_x = np.unique(offspec_data.T[0])
    xbins = len(unique_x)
    unique_x = np.unique(offspec_data.T[1])
    zbins = len(unique_x)

    print("\n\nFile: %s" % file_path)
    print("Binning: %s %s [%s]" %(xbins, zbins, xbins*zbins))

    off = np.reshape(offspec_data, (zbins, xbins, offspec_data.shape[1]))

    dk = (off.T[0]).T[0]
    qz = (off.T[1])[0]

    quick_intensity = off.T[2].T
    
    if q_axis:
        if width>0:
            refl = np.sum(quick_intensity.T[index-width:index+width+1], axis=0)
            refl /= 1.0 #width
        else:
            refl = quick_intensity.T[index]
        _index_value = dk[index]
    else:
        refl = quick_intensity[index]
        _index_value = qz[index]

    scale = np.max(quick_intensity)
    #scale = np.max(refl)
    #scale = 1
    quick_intensity /= scale
    quick_intensity[quick_intensity<1.0e-9] = 1.0e-9

    print("Scale = %s" % scale)
    print("Const value = %s" % _index_value)
    print("Width = %s" % width)
    return [qz, refl/scale], dk, qz, quick_intensity


# Smooth dTOF=400 usec

In [6]:
_spec_400, dk, qz, off_spec = load_data('/SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_OffSpecSmooth_Off_Off_v2_TOF_400.dat',
                                       index=42, q_axis=True, width=5)

plot_heatmap(dk, qz, np.log(off_spec), x_title='', y_title='', surface=False,
                 x_log=False, y_log=False)

(23688, 3)


File: /SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_OffSpecSmooth_Off_Off_v2_TOF_400.dat
Binning: 84 282 [23688]
Scale = 9.30532
Const value = 0.000180723
Width = 5


# Binned dTOF=400 usec

In [7]:
_spec_binned_400, dk, qz, off_spec = load_data('/SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_OffSpecBinned_Off_Off_v2_TOF_400.dat',
                                      index=42, q_axis=True, width=5)

plot_heatmap(dk, qz, np.log(off_spec), x_title='', y_title='', surface=False,
                 x_log=False, y_log=False)

(23688, 4)


File: /SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_OffSpecBinned_Off_Off_v2_TOF_400.dat
Binning: 84 282 [23688]
Scale = 10.7166
Const value = 0.000178571
Width = 5


# Smooth dTOF=40 usec

In [8]:
_spec_40, dk, qz, off_spec = load_data('/SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_OffSpecSmooth_Off_Off_v2_TOF_40.dat',
                                      index=42, q_axis=True, width=5)

plot_heatmap(dk, qz, np.log(off_spec), x_title='', y_title='', surface=False,
                 x_log=False, y_log=False)


(23688, 3)


File: /SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_OffSpecSmooth_Off_Off_v2_TOF_40.dat
Binning: 84 282 [23688]
Scale = 8.62366
Const value = 0.000180723
Width = 5


# Binned dTOF=40 usec

In [9]:
_spec_binned_40, dk, qz, off_spec = load_data('/SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_OffSpecBinned_Off_Off_v2_TOF_40.dat',
                                      index=42, q_axis=True, width=10)

plot_heatmap(dk, qz, np.log(off_spec), x_title='', y_title='', surface=False,
                 x_log=False, y_log=False)


(23688, 4)


File: /SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_OffSpecBinned_Off_Off_v2_TOF_40.dat
Binning: 84 282 [23688]
Scale = 10.6088
Const value = 0.000178571
Width = 10


In [17]:
refl_400_cstq = np.loadtxt('/SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_Specular_Off_Off_CSTQ_v2_TOF_400.dat')
refl_40_cstq = np.loadtxt('/SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_Specular_Off_Off_CSTQ_v2_TOF_40.dat')
refl_400 = np.loadtxt('/SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_Specular_Off_Off_v2_TOF_400.dat')
refl_40 = np.loadtxt('/SNS/users/m2d/git/reflectivity_ui/test/notebooks/data/REF_M_30889+30890_Specular_Off_Off_v2_TOF_40.dat')

_scale = 1.0/2.8
_plot_list = [[_spec_400[0], _scale*_spec_400[1]],
              [_spec_40[0], _scale*_spec_40[1]],
              [_spec_binned_400[0], _scale*_spec_binned_400[1]],
              [_spec_binned_40[0], _scale*_spec_binned_40[1]],
             [refl_400_cstq.T[0], refl_400_cstq.T[1], refl_400_cstq.T[2]],
             [refl_40_cstq.T[0], refl_40_cstq.T[1], refl_40_cstq.T[2]],
             [refl_400.T[0], refl_400.T[1], refl_400.T[2]],
             [refl_40.T[0], refl_40.T[1], refl_40.T[2]],]
_plot_names = ["Spec 2D [400]", "Spec 2D [40]", "Spec 2D binned [400]", "Spec 2D binned [40]",
              "Spec 1D cst-q [400]", "Spec 1D cst-q [40]", "Spec 1D [400]", "Spec 1D [40]"]
plot1d(_plot_list, _plot_names,
           x_title='', y_title='',
           x_log=False, y_log=True, show_dx=True)

